In [4]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

In [5]:
path = '/opt/ml/data/'

users = pd.read_csv(path+'users.csv')
books = pd.read_csv(path+'books.csv')
train_ratings = pd.read_csv(path+'train_ratings.csv')
test_ratings = pd.read_csv(path + 'test_ratings.csv')
sample_submission = pd.read_csv(path+'sample_submission.csv')

print('users shape: ', users.shape)
print('books shape: ', books.shape)
print('train_ratings shape: ', train_ratings.shape)
print(test_ratings.shape)
print(sample_submission.shape)

users shape:  (68092, 3)
books shape:  (149570, 10)
train_ratings shape:  (306795, 3)
(76699, 3)
(76699, 3)


In [6]:
users.isna().sum()

user_id         0
location        0
age         27833
dtype: int64

In [7]:
books.isna().sum()

isbn                       0
book_title                 0
book_author                0
year_of_publication        0
publisher                  0
img_url                    0
language               67227
category               68851
summary                67227
img_path                   0
dtype: int64

In [8]:
train_ratings.isna().sum()

user_id    0
isbn       0
rating     0
dtype: int64

In [9]:
users['location'] = users['location'].str.replace(r'[^0-9a-zA-Z:,]', '') 

users['location_city'] = users['location'].apply(lambda x: x.split(',')[0].strip())
users['location_state'] = users['location'].apply(lambda x: x.split(',')[1].strip())
users['location_country'] = users['location'].apply(lambda x: x.split(',')[2].strip())

users = users.replace('na', np.nan) 
users = users.replace('', np.nan)

/tmp/ipykernel_48997/3958095115.py:1: FutureWarning: The default value of regex will change from True to False in a future version.
  users['location'] = users['location'].str.replace(r'[^0-9a-zA-Z:,]', '')


In [10]:
users.isna().sum()

user_id                 0
location                0
age                 27833
location_city         122
location_state       3254
location_country     2124
dtype: int64

In [11]:
users[users['location_city'].isna()&users['location_state'].isna()&users['location_country'].isna()].shape

(9, 6)

In [12]:
from collections import Counter

city_base_data = Counter(users['location']).most_common()

for i in city_base_data:
    users.loc[users[users['location_city']==i[0].split(',')[0]].index,'location_state'] = i[0].split(',')[1]
    users.loc[users[users['location_city']==i[0].split(',')[0]].index,'location_country'] = i[0].split(',')[2]

In [13]:
pd.DataFrame(city_base_data)

0    1
0            toronto,ontario,canada  616
1               portland,oregon,usa  540
2            seattle,washington,usa  536
3              chicago,illinois,usa  503
4       sanfrancisco,california,usa  458
...                             ...  ...
18052   copenhagens,sjlland,denmark    1
18053  grasse,alpesmaritimes,france    1
18054            na,manitoba,canada    1
18055      victoria,delaware,canada    1
18056         irvington,alabama,usa    1

[18057 rows x 2 columns]

In [14]:
print(len(city_base_data))
print(pd.DataFrame(city_base_data)[0].nunique())

18057
18057


In [15]:
users.isna().sum()

user_id                 0
location                0
age                 27833
location_city         122
location_state         58
location_country       11
dtype: int64

In [16]:
users[users['location_city'].isna()]

user_id                 location   age location_city location_state  \
2        11676                 na,na,na   NaN           NaN            NaN   
1008     48630         na,newjersey,usa  34.0           NaN      newjersey   
1012     49460              ,kansas,usa  37.0           NaN         kansas   
1065     56399  na,surrey,unitedkingdom  63.0           NaN         surrey   
1200     75081            ,illinois,usa  29.0           NaN       illinois   
...        ...                      ...   ...           ...            ...   
67067   216272        ,newhampshire,usa   NaN           NaN   newhampshire   
67104   218092                   na,na,   NaN           NaN            NaN   
67402   234041             na,na,sweden  21.0           NaN            NaN   
67805   258088      ,iledefrance,france  30.0           NaN    iledefrance   
68084   278248       na,manitoba,canada   NaN           NaN       manitoba   

      location_country  
2                  NaN  
1008               usa  
1012               usa  
1065     unitedkingdom  
1200               usa  
...                ...  
67067              usa  
67104              NaN  
67402           sweden  
67805           france  
68084           canada  

[122 rows x 6 columns]

In [17]:
for i in city_base_data:
    users.loc[users[users['location_city'].isna() & users['location_state']==i[0].split(',')[1]].index,'location_city'] = i[0].split(',')[0]

In [18]:
users.isna().sum()

user_id                 0
location                0
age                 27833
location_city         122
location_state         58
location_country       11
dtype: int64

age는 카테고리를 사용하여 결측값채우자. 이거 아니면 그냥 20~30랜덤이나 국가별 평균으로 박는게 나음.

In [19]:
users

user_id                         location   age location_city  \
0            8           timmins,ontario,canada   NaN       timmins   
1        11400            ottawa,ontario,canada  49.0        ottawa   
2        11676                         na,na,na   NaN           NaN   
3        67544           toronto,ontario,canada  30.0       toronto   
4        85526  victoria,britishcolumbia,canada  36.0      victoria   
...        ...                              ...   ...           ...   
68087   278376        danville,pennsylvania,usa  54.0      danville   
68088   278621         victoria,delaware,canada  74.0      victoria   
68089   278636            irvington,alabama,usa   NaN     irvington   
68090   278659         vancouver,washington,usa  33.0     vancouver   
68091   278713        albuquerque,newmexico,usa  63.0   albuquerque   

      location_state location_country  
0            ontario           canada  
1             kansas              usa  
2                NaN              NaN  
3             oregon           canada  
4           delaware           canada  
...              ...              ...  
68087   newhampshire              usa  
68088       delaware           canada  
68089        alabama              usa  
68090                              bc  
68091                       newmexico  

[68092 rows x 6 columns]

# books 처리

In [20]:
books = pd.read_csv(path+'books.csv')

In [21]:
books.sample(10)

isbn                                         book_title  \
50454   0140367292                    No Gun for Asmir (Puffin Books)   
75011   3785532024  WahnsinnsWissen. Ein Knaller, die Chemie. ( Ab...   
142047  0689315759                 Black Unicorn (Dragonflight Books)   
8241    006106498X  Wishbone Classic #11 Adv of Tom Sawyer (Wishbone)   
121479  059060385X  The Berenstain Bear Scouts and the Sci-Fi Pizz...   
112593  1564967743  Graphic Designer's Digital Printing and Prepre...   
8327    0844273252                            Guide to Spanish Idioms   
53065   0671017373           Fire Water (Peter Bartholomew Mysteries)   
66952   0451405455       The Raven's Wish (Topaz Historical Romances)   
67060   0425157709  Airborne: A Guided Tour of an Airborne Task Force   

                  book_author  year_of_publication                 publisher  \
50454   Christobel Mattingley               1994.0              Puffin Books   
75011             Nick Arnold               1998.0              Loewe Verlag   
142047             Tanith Lee               1991.0            Atheneum Books   
8241          Stephen Fuentes               1997.0       HarperEntertainment   
121479        Stan Berenstain               1996.0                Scholastic   
112593       Constance Sidles               2001.0       Rockport Publishers   
8327       Raymond H. Pierson               1985.0               McGraw-Hill   
53065           Sally Gunning               1999.0                    Pocket   
66952              Susan King               1995.0                     Topaz   
67060              Tom Clancy               1997.0  Berkley Publishing Group   

                                                  img_url language  \
50454   http://images.amazon.com/images/P/0140367292.0...       en   
75011   http://images.amazon.com/images/P/3785532024.0...      NaN   
142047  http://images.amazon.com/images/P/0689315759.0...       en   
8241    http://images.amazon.com/images/P/006106498X.0...       en   
121479  http://images.amazon.com/images/P/059060385X.0...       en   
112593  http://images.amazon.com/images/P/1564967743.0...       en   
8327    http://images.amazon.com/images/P/0844273252.0...       en   
53065   http://images.amazon.com/images/P/0671017373.0...       en   
66952   http://images.amazon.com/images/P/0451405455.0...      NaN   
67060   http://images.amazon.com/images/P/0425157709.0...       en   

                          category  \
50454      ['Juvenile Nonfiction']   
75011                          NaN   
142047                ['Artisans']   
8241          ['Juvenile Fiction']   
121479        ['Juvenile Fiction']   
112593                  ['Design']   
8327    ['Foreign Language Study']   
53065                  ['Fiction']   
66952                          NaN   
67060                  ['History']   

                                                  summary  \
50454   War has come to Asmir&#39;s home in Sarajevo. ...   
75011                                                 NaN   
142047  With her talent for mending things, sixteen-ye...   
8241    The adventures of a mischievous young boy and ...   
121479  Evil Weasel McGreed&#39;s got the flying secre...   
112593  Constance Sidles argues that such all-too-freq...   
8327    Guide to Spanish Idioms is packed with more th...   
53065   Peter and Connie Bartholomew are stunned when ...   
66952                                                 NaN   
67060   A behind-the-scenes look at the elite branch o...   

                                 img_path  
50454   images/0140367292.01.THUMBZZZ.jpg  
75011   images/3785532024.01.THUMBZZZ.jpg  
142047  images/0689315759.01.THUMBZZZ.jpg  
8241    images/006106498X.01.THUMBZZZ.jpg  
121479  images/059060385X.01.THUMBZZZ.jpg  
112593  images/1564967743.01.THUMBZZZ.jpg  
8327    images/0844273252.01.THUMBZZZ.jpg  
53065   images/0671017373.01.THUMBZZZ.jpg  
66952   images/0451405455.01.THUMBZZZ.jpg  
67060   images/0425157709.0

In [22]:
books.isna().sum()

isbn                       0
book_title                 0
book_author                0
year_of_publication        0
publisher                  0
img_url                    0
language               67227
category               68851
summary                67227
img_path                   0
dtype: int64

In [23]:
books['category'].unique()

array(["['Actresses']", "['1940-1949']", "['Medical']", ...,
       "['Deafness']", "['Alternative histories']",
       "['Authors, Canadian (English) 20th century Biography']"],
      dtype=object)

In [24]:
books['category'].nunique()

4292

In [25]:
books['isbn'] = books['img_url'].apply(lambda x: x.split('P/')[1][:10])

In [26]:
books.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 149570 entries, 0 to 149569
Data columns (total 10 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   isbn                 149570 non-null  object 
 1   book_title           149570 non-null  object 
 2   book_author          149570 non-null  object 
 3   year_of_publication  149570 non-null  float64
 4   publisher            149570 non-null  object 
 5   img_url              149570 non-null  object 
 6   language             82343 non-null   object 
 7   category             80719 non-null   object 
 8   summary              82343 non-null   object 
 9   img_path             149570 non-null  object 
dtypes: float64(1), object(9)
memory usage: 11.4+ MB


1. 1950 년도 이하 데이터 지우기.

In [27]:
books['year_of_publication'].value_counts().sort_index()

1376.0        1
1378.0        1
1806.0        1
1900.0        1
1901.0        4
          ...  
2002.0    11669
2003.0     9430
2004.0     3771
2005.0       19
2006.0        1
Name: year_of_publication, Length: 95, dtype: int64

In [28]:
books.drop(books[books['year_of_publication']<1950].index,axis=0,inplace=True)

In [29]:
books['year_of_publication'].value_counts().sort_index()

1950.0       16
1951.0       20
1952.0       20
1953.0       48
1954.0       30
1955.0       45
1956.0       31
1957.0       47
1958.0       45
1959.0       60
1960.0       65
1961.0       76
1962.0       73
1963.0       70
1964.0       72
1965.0       94
1966.0       92
1967.0       89
1968.0      124
1969.0      178
1970.0      221
1971.0      249
1972.0      366
1973.0      410
1974.0      440
1975.0      541
1976.0      697
1977.0      837
1978.0      944
1979.0      931
1980.0     1088
1981.0     1438
1982.0     1848
1983.0     1972
1984.0     2214
1985.0     2433
1986.0     2616
1987.0     2976
1988.0     3473
1989.0     3751
1990.0     4279
1991.0     4692
1992.0     5209
1993.0     5554
1994.0     9058
1995.0     7494
1996.0     7853
1997.0     8439
1998.0     9300
1999.0    10480
2000.0    10391
2001.0    11020
2002.0    11669
2003.0     9430
2004.0     3771
2005.0       19
2006.0        1
Name: year_of_publication, dtype: int64

# 출판사 조지기.
- 굳이?... Harlequin 출판사랑 앞자리 4개 같은거 Silhouette출판사인데 이 출판사 개수가 1600개다. 이 정도면 다른 출판사로 봐야하지 않나. 출판사 책 1개들인 것들이 좀 많은데 이거 좀 치워볼까?

In [30]:
books['publisher'].value_counts()[-10000]

9

In [31]:
books['publisher'].value_counts()

Harlequin                     3004
Ballantine Books              2322
Pocket                        2274
Penguin Books                 1942
Bantam Books                  1937
                              ... 
Ediciones Xandro                 1
Jarrold Pub                      1
Kiepenheuer                      1
Rainbow Pyramid Publishers       1
American Map Corporation         1
Name: publisher, Length: 11562, dtype: int64

In [32]:
books['publisher'].nunique()

11562

In [33]:
books['publisher'].value_counts().values[-7000]

2

In [34]:
books['isbn'].apply(lambda x:x[2:6])

0         0200
1         6097
2         7415
3         9913
4         2517
          ... 
149565    7161
149566    6790
149567    8415
149568    1233
149569    6966
Name: isbn, Length: 149399, dtype: object

In [35]:
for pn in books['isbn'].apply(lambda x:x[2:6]):
    if('A' in pn or 'B' in pn or 'C' in pn or 'D' in pn or 'G' in pn):
        print(pn)

000D
000A
000D
001G
000C
000A
000A
000C
000D
000D


In [36]:
from collections import defaultdict
d = [defaultdict(lambda :0)] * 10000 # == defaultdict(int)

for pn in books['isbn'].apply(lambda x:x[2:6]):
    if('A' in pn or 'B' in pn or 'C' in pn or 'D' in pn or 'F' in pn):
        print(pn)
    



000D
000A
000D
000C
001F
000A
000A
000C
001F
000D
001F
000D


In [37]:
books[books['isbn'].apply(lambda x:x[2:6]) == '000A']

isbn                  book_title              book_author  \
15104  B0000A2U93                    Carmilla  Joseph Sheridan Le Fanu   
78170  B0000AA9JB  A Darkness More Than Night         Michael Connelly   
82023  B0000AZW79             O Is for Outlaw              Sue Grafton   

       year_of_publication                   publisher  \
15104               1994.0           Soft Editions Ltd   
78170               2001.0      Little Brown & Company   
82023               1999.0  Henry Holt & Company, Inc.   

                                                 img_url language category  \
15104  http://images.amazon.com/images/P/B0000A2U93.0...      NaN      NaN   
78170  http://images.amazon.com/images/P/B0000AA9JB.0...      NaN      NaN   
82023  http://images.amazon.com/images/P/B0000AZW79.0...      NaN      NaN   

      summary                           img_path  
15104     NaN  images/B0000A2U93.01.THUMBZZZ.jpg  
78170     NaN  images/B0000AA9JB.01.THUMBZZZ.jpg  
82023     NaN  images/B0000AZW79.01.THUMBZZZ.jpg

In [38]:
books[books['isbn'].apply(lambda x:x[:4])=='0373'].sample(5)

isbn                                         book_title  \
140057  0373273800               Shotgun Honeymoon (Intimate Moments)   
135525  0373257856  Manhunting In Mississippi (Manhunting...) (Tem...   
5414    0373075944  Devil And Jessie Webster (Silhouette Intimate ...   
120399  0373119054  Ideal Marriage  (Top Author) (Harlequin Presen...   
88559   0373835019             Take 5: Volume #5: Tender Love Stories   

           book_author  year_of_publication   publisher  \
140057    Terese Ramin               2004.0  Silhouette   
135525  Stephanie Bond               1998.0   Harlequin   
5414       Lydia Burke               1994.0  Silhouette   
120399  Helen Bianchin               1997.0   Harlequin   
88559   Kasey Michaels               2002.0   Harlequin   

                                                  img_url language  \
140057  http://images.amazon.com/images/P/0373273800.0...      NaN   
135525  http://images.amazon.com/images/P/0373257856.0...      NaN   
5414    http://images.amazon.com/images/P/0373075944.0...       en   
120399  http://images.amazon.com/images/P/0373119054.0...       en   
88559   http://images.amazon.com/images/P/0373835019.0...       en   

           category                                            summary  \
140057          NaN                                                NaN   
135525          NaN                                                NaN   
5414    ['Fiction']  The Devil And Jessie Webster by Lydia Burke re...   
120399  ['Fiction']  An Ideal Marriage? by Helen Bianchin released ...   
88559   ['Fiction']  Take 5 Volume #5 by Kasey Michaels\Day Leclair...   

                                 img_path  
140057  images/0373273800.01.THUMBZZZ.jpg  
135525  images/0373257856.01.THUMBZZZ.jpg  
5414    images/0373075944.01.THUMBZZZ.jpg  
120399  images/0373119054.01.THUMBZZZ.jpg  
88559   images/0373835019.01.THUMBZZZ.jpg

In [39]:
books[books['publisher']=='Silhouette']

isbn                                         book_title  \
147     0373196407                                 The Prince's Tutor   
212     0373483880    The Macgregors: Serena - Caine (The Macgregors)   
336     0373218400                                      Table For Two   
342     0373241739  Stallion Tamer (Cowboys Of The Southwest) (Spe...   
343     0373242441  Dream Groom  (Brides Of Bradley House) (Silhou...   
...            ...                                                ...   
148408  0373089457         Lucky Penny (Silhouette Romance, No. 8945)   
148836  0373053193                                  Too Hot To Handle   
148837  0373055463           Fire and Rain (Silhouette Desire No 546)   
149482  0373762380  Cinderella'S Tycoon  (Texas Cattleman'S Club) ...   
149523  0373071388    Illusions (Silhouette Intimate Moments, No 138)   

             book_author  year_of_publication   publisher  \
147       Nicole Burnham               2003.0  Silhouette   
212         Nora Roberts               1998.0  Silhouette   
336         Nora Roberts               2002.0  Silhouette   
342      Lindsay McKenna               1998.0  Silhouette   
343        Susan Mallery               1999.0  Silhouette   
...                  ...                  ...         ...   
148408  Elizabeth August               1993.0  Silhouette   
148836  Elizabeth Lowell               1986.0  Silhouette   
148837  Elizabeth Lowell               1989.0  Silhouette   
149482    Caroline Cross               1999.0  Silhouette   
149523     Eve Gladstone               1986.0  Silhouette   

                                                  img_url language  \
147     http://images.amazon.com/images/P/0373196407.0...      NaN   
212     http://images.amazon.com/images/P/0373483880.0...       en   
336     http://images.amazon.com/images/P/0373218400.0...       en   
342     http://images.amazon.com/images/P/0373241739.0...       en   
343     http://images.amazon.com/images/P/0373242441.0...      NaN   
...                                                   ...      ...   
148408  http://images.amazon.com/images/P/0373089457.0...      NaN   
148836  http://images.amazon.com/images/P/0373053193.0...       en   
148837  http://images.amazon.com/images/P/0373055463.0...       en   
149482  http://images.amazon.com/images/P/0373762380.0...       en   
149523  http://images.amazon.com/images/P/0373071388.0...      NaN   

            category                                            summary  \
147              NaN                                                NaN   
212      ['Fiction']  The MacGregors; Serena &amp; Caine by Nora Rob...   
336      ['Fiction']  Table For Two by Nora Roberts released on Oct ...   
342      ['Fiction']  Stallion Tamer by Lindsay McKenna released on ...   
343              NaN                                                NaN   
...              ...                                                ...   
148408           NaN                                                NaN   
148836    ['Divers']  Competitive diver Tory Wells is recovering fro...   
148837  ['Colorado']  Luke MacKenzie vowed he could never fall for h...   
149482   ['Fiction']  Cinderella&#39;s Tycoon by Caroline Cross rele...   
149523           NaN                                                NaN   

                                 img_path  
147     images/0373196407.01.THUMBZZZ.jpg  
212     images/0373483880.01.THUMBZZZ.jpg  
336     images/0373218400.01.THUMBZZZ.jpg  
342     images/0373241739.01.THUMBZZZ.jpg  
343     images/0373242441.01.THUMBZZZ.jpg  
...                                   ...  
148408  images/0373089457.01.THUMBZZZ.jpg  
148836  images/0373053193.01.THUMBZZZ.jpg  
148837  images/0373055463.01.THUMBZZZ.jpg  
149482  images/0373762380.01.THUMBZZZ.jpg  
149523  images/0373071388.01.THUMBZZZ.jpg  

[1684 rows x 10 columns]

In [40]:
from collections import defaultdict
d = [defaultdict(lambda :0) for _ in range(10000)]  # == defaultdict(int), ! [defaultdict(lambda :0)] * 10000 하면 얕은 복사다. defaultdict 10000개가 서로 공유함.

for pn,publisher  in zip(books['isbn'].apply(lambda x:x[2:6]), books['publisher']):
    try:
        pn=int(pn)
    except:
        continue

    print(pn, publisher)
    d[pn][publisher] += 1

    

200 HarperFlamingo Canada
6097 HarperPerennial
7415 Farrar Straus Giroux
9913 Putnam Pub Group
2517 Berkley Publishing Group
7187 Audioworks
4322 Scribner
7107 Emblem Editions
8784 House of Anansi Press
5204 Mira Books
5874 Health Communications
6740 Brilliance Audio - Trade
7566 Kensington Publishing Corp.
8132 River City Pub
4023 Dell
5226 Plume
980 Three Rivers Press
4172 Ryland Peters & Small Ltd
7938 Cypress House
6107 HarperEntertainment
3909 Scholastic
8982 Aladdin
7188 Too Far
4540 Ballantine Books
4541 Ballantine Books
1297 St. Martin's Paperbacks
2509 Berkley Publishing Group
5326 Bantam Books
5327 Spectra
8482 Scribner
9107 Crossway Books
9107 Crossway Books
7575 Random House Trade Paperbacks
2516 Berkley Publishing Group
492 LÃ?Â¼bbe
7540 Alfred A. Knopf
4631 Little Brown & Company
4900 Ballantine Books
6016 Harpercollins
8078 Avon
7176 Fireside
6109 HarperTorch
5358 Bantam Books
7188 Pocket
5358 Bantam Books
2518 Berkley Publishing Group
2518 Berkley Publishing Group
4022 

In [41]:
modify_publisher = []

print(sorted(d[7303].items(),key = lambda x:-x[1]))

[('Harlequin', 281), ('Faith & Life Press', 1), ('Samuel French', 1), ('Snosrap Publishing', 1), ('McGraw-Hill/Dushkin', 1)]


In [42]:
for s_d in d:
    try:
        modify_publisher.append(sorted(s_d.items(),key = lambda x:-x[1])[0][0])
    except:
        modify_publisher.append('None')
    

In [43]:
modify_publisher[7303]

'Harlequin'

In [44]:
modify_publisher[200]

'HarperFlamingo Canada'

In [45]:
modify_publisher[7415]

'Farrar Straus Giroux'

In [46]:
modify_publisher[2517]

'Berkley Publishing Group'

In [47]:
modify_publisher[6097]

'Perennial'

In [48]:
d[6097]

defaultdict(<function __main__.<listcomp>.<lambda>()>,
            {'HarperPerennial': 1,
             'Perennial': 105,
             'Harpercollins': 46,
             'HarperCollins': 8,
             'Perennial Currents': 6,
             'Fantagraphics Books': 24,
             'Perennial Library': 4,
             'Fantagraphics (not W.W. Norton)': 1,
             'HarperCollins Publishers': 2,
             'Harpercollins Publisher': 1,
             'Perennial (HarperCollins)': 1,
             'Harper Audio': 1,
             'Quill': 1})

In [65]:
books['publisher'].nunique()

11562

In [66]:
books

isbn                                         book_title  \
0       0002005018                                       Clara Callan   
1       0060973129                               Decision in Normandy   
2       0374157065  Flu: The Story of the Great Influenza Pandemic...   
3       0399135782                             The Kitchen God's Wife   
4       0425176428  What If?: The World's Foremost Military Histor...   
...            ...                                                ...   
149565  067161746X  The Bachelor Home Companion: A Practical Guide...   
149566  0767907566  All Elevations Unknown: An Adventure in the He...   
149567  0884159221  Why stop?: A guide to Texas historical roadsid...   
149568  0912333022  The Are You Being Served? Stories: 'Camping In...   
149569  1569661057  Dallas Street Map Guide and Directory, 2000 Ed...   

                 book_author  year_of_publication                 publisher  \
0       Richard Bruce Wright               2001.0     HarperFlamingo Canada   
1               Carlo D'Este               1991.0           HarperPerennial   
2           Gina Bari Kolata               1999.0      Farrar Straus Giroux   
3                    Amy Tan               1991.0          Putnam Pub Group   
4              Robert Cowley               2000.0  Berkley Publishing Group   
...                      ...                  ...                       ...   
149565         P.J. O'Rourke               1987.0              Pocket Books   
149566          Sam Lightner               2001.0            Broadway Books   
149567         Claude Dooley               1985.0           Lone Star Books   
149568          Jeremy Lloyd               1997.0                Kqed Books   
149569                Mapsco               1999.0  American Map Corporation   

                                                  img_url language   category  \
0       http://images.amazon.com/images/P/0002005018.0...       en  actresses   
1       http://images.amazon.com/images/P/0060973129.0...       en  1940 1949   
2       http://images.amazon.com/images/P/0374157065.0...       en    medical   
3       http://images.amazon.com/images/P/0399135782.0...       en    fiction   
4       http://images.amazon.com/images/P/0425176428.0...       en    history   
...                                                   ...      ...        ...   
149565  http://images.amazon.com/images/P/067161746X.0...       en      humor   
149566  http://images.amazon.com/images/P/0767907566.0...       en     nature   
149567  http://images.amazon.com/images/P/0884159221.0...      NaN        NaN   
149568  http://images.amazon.com/images/P/0912333022.0...       en    fiction   
149569  http://images.amazon.com/images/P/1569661057.0...      NaN        NaN   

                                                  summary  \
0       In a small town in Canada, Clara Callan reluct...   
1       Here, for the first time in paperback, is an o...   
2       Describes the great flu epidemic of 1918, an o...   
3       A Chinese immigrant who is convinced she is dy...   
4       Essays by respected military historians, inclu...   
...                                                   ...   
149565  A tongue-in-cheek survival guide for single pe...   
149566  A daring twist on the travel-adventure genre t...   
149567                                                NaN   
149568  These hilarious stories by the creator of publ...   
149569                                                NaN   

                                 img_path  
0       images/0002005018.01.THUMBZZZ.jpg  
1       images/0060973129.01.THUMBZZZ.jpg  
2       images/0374157065.01.THUMBZZZ.jpg  
3       images/0399135782.01.THUMBZZZ.jpg  
4       images/0425176428.01.THUMBZZZ.jpg  
...                                   ...  
149565  images/067161746X.01.THUMBZZZ.jpg  
149566  images/0767907566.01.THUMBZZZ.jpg  
149567  images/0884159221.01.THUMBZZZ.jpg  
149568  images/0912333022.01.THUMBZZZ.jpg 

In [67]:
books['isbn'].apply(lambda x:x[2:6])

0         0200
1         6097
2         7415
3         9913
4         2517
          ... 
149565    7161
149566    6790
149567    8415
149568    1233
149569    6966
Name: isbn, Length: 149399, dtype: object

In [68]:
for i in range(10000):
    books[books['isbn'].apply(lambda x:x[2:6]) == i]['publisher'] = modify_publisher[i]

In [69]:
books['publisher'].nunique()

11562

- Publisher EDA 미션에 나온거 대로 해서 성능 비교해보기.
- Language, Category 결측치 채우기.
- Category 기반으로 나이대 결측치 채워 넣기.

In [70]:
import re
books.loc[books[books['category'].notnull()].index, 'category'] = books[books['category'].notnull()]['category'].apply(lambda x:re.sub('[\W_]+',' ',x).strip())

In [71]:
books['category'].value_counts()

fiction                                            33009
juvenile fiction                                    5816
biography autobiography                             3326
history                                             1926
religion                                            1815
                                                   ...  
gone with the wind motion picture 1939                 1
disguise                                               1
country lawyers                                        1
humorous stories brazilian                             1
authors canadian english 20th century biography        1
Name: category, Length: 4103, dtype: int64

In [72]:
books['category']=books['category'].str.lower()

In [73]:
books['category'].nunique()

4103

In [74]:
books['category']

0         actresses
1         1940 1949
2           medical
3           fiction
4           history
            ...    
149565        humor
149566       nature
149567          NaN
149568      fiction
149569          NaN
Name: category, Length: 149399, dtype: object

In [100]:
context_df = train_ratings.merge(users, on='user_id', how='left').merge(books[['isbn', 'category', 'publisher', 'language', 'book_author']], on='isbn', how='left')

In [101]:
from collections import Counter
Counter(list(list(context_df.groupby('category')['age'])[0][1]))

Counter({25.0: 1, 33.0: 1})

In [102]:
len(list(context_df.groupby('category')['age']))

3713

In [103]:
context_df.fillna(-1)

user_id        isbn  rating                   location   age  \
0             8  0002005018       4     timmins,ontario,canada  -1.0   
1         67544  0002005018       7     toronto,ontario,canada  30.0   
2        123629  0002005018       8    kingston,ontario,canada  -1.0   
3        200273  0002005018       8      comber,ontario,canada  -1.0   
4        210926  0002005018       9      guelph,ontario,canada  -1.0   
...         ...         ...     ...                        ...   ...   
306790   278843  0743525493       7  pismobeach,california,usa  28.0   
306791   278851  067161746X       6           dallas,texas,usa  33.0   
306792   278851  0884159221       7           dallas,texas,usa  33.0   
306793   278851  0912333022       7           dallas,texas,usa  33.0   
306794   278851  1569661057      10           dallas,texas,usa  33.0   

       location_city location_state location_country   category  \
0            timmins        ontario           canada  actresses   
1            toronto         oregon           canada  actresses   
2           kingston         hobart         tasmania  actresses   
3             comber        ontario           canada  actresses   
4             guelph                                  actresses   
...              ...            ...              ...        ...   
306790    pismobeach     california              usa         -1   
306791        dallas          texas                       humor   
306792        dallas          texas                          -1   
306793        dallas          texas                     fiction   
306794        dallas          texas                          -1   

                       publisher language           book_author  
0          HarperFlamingo Canada       en  Richard Bruce Wright  
1          HarperFlamingo Canada       en  Richard Bruce Wright  
2          HarperFlamingo Canada       en  Richard Bruce Wright  
3          HarperFlamingo Canada       en  Richard Bruce Wright  
4          HarperFlamingo Canada       en  Richard Bruce Wright  
...                          ...      ...                   ...  
306790    Simon & Schuster Audio       -1         David Gardner  
306791              Pocket Books       en         P.J. O'Rourke  
306792           Lone Star Books       -1         Claude Dooley  
306793                Kqed Books       en          Jeremy Lloyd  
306794  American Map Corporation       -1                Mapsco  

[306795 rows x 12 columns]

In [79]:
category_age_table = list(context_df.groupby('category')['age'])

category_age_dict=dict()

for ca in category_age_table:
    category_age_dict[ca[0]] = Counter(list(ca[1])).most_common(1)[0]


In [104]:
category_age_dict

{'0': (25.0, 1),
 '0islands': (36.0, 1),
 '11030 fiction in english 1900 1945 60030 texts': (nan, 1),
 '11030 short stories in english p1030 canadian writers 1945 60030 texts': (24.0,
  1),
 '1900 1999': (31.0, 1),
 '1940 1949': (71.0, 1),
 '20th century general fiction': (29.0, 1),
 '364614153': (32.0, 1),
 '87th precinct imaginary place': (nan, 1),
 'a grow and learn library': (51.0, 1),
 'aanhalings engels': (38.0, 1),
 'aardvark': (nan, 1),
 'abandoned children': (22.0, 2),
 'abbeys': (42.0, 1),
 'abbreviations': (21.0, 1),
 'abc s': (36.0, 1),
 'abdomen': (28.0, 1),
 'abduction': (32.0, 2),
 'aberdeen scotland': (31.0, 1),
 'ability': (17.0, 1),
 'abnormal reflexes': (48.0, 1),
 'aboriginal': (19.0, 1),
 'aboriginal australians': (23.0, 2),
 'abortion': (51.0, 3),
 'abraham lincoln': (nan, 1),
 'abscam bribery scandal 1980': (57.0, 1),
 'absence and presumption of death': (38.0, 1),
 'absentee mothers': (nan, 1),
 'abused children': (31.0, 2),
 'abused wives': (46.0, 2),
 'abused 

In [105]:
print(category_age_dict['drama'])

(24.0, 35)


In [87]:
print(category_age_dict['humor'])

(29.0, 127)


In [88]:
print(category_age_dict['fiction'])

(52.0, 3825)


In [106]:
context_df.isna().sum()

user_id                  0
isbn                     0
rating                   0
location                 0
age                  92662
location_city         7008
location_state        5826
location_country      5535
category            121326
publisher              252
language            119195
book_author            252
dtype: int64

In [96]:
for i, v in context_df.iterrows():
    if(v['age']!=v['age'] and v['category']==v['category']):
        c = category_age_dict[v['category']][0]
        if(c == c):
            context_df.loc[i,'age'] = c

In [107]:
context_df
#나이 결측치 채우면 자연스럽게 category도 채워짐.

user_id        isbn  rating                   location   age  \
0             8  0002005018       4     timmins,ontario,canada   NaN   
1         67544  0002005018       7     toronto,ontario,canada  30.0   
2        123629  0002005018       8    kingston,ontario,canada   NaN   
3        200273  0002005018       8      comber,ontario,canada   NaN   
4        210926  0002005018       9      guelph,ontario,canada   NaN   
...         ...         ...     ...                        ...   ...   
306790   278843  0743525493       7  pismobeach,california,usa  28.0   
306791   278851  067161746X       6           dallas,texas,usa  33.0   
306792   278851  0884159221       7           dallas,texas,usa  33.0   
306793   278851  0912333022       7           dallas,texas,usa  33.0   
306794   278851  1569661057      10           dallas,texas,usa  33.0   

       location_city location_state location_country   category  \
0            timmins        ontario           canada  actresses   
1            toronto         oregon           canada  actresses   
2           kingston         hobart         tasmania  actresses   
3             comber        ontario           canada  actresses   
4             guelph                                  actresses   
...              ...            ...              ...        ...   
306790    pismobeach     california              usa        NaN   
306791        dallas          texas                       humor   
306792        dallas          texas                         NaN   
306793        dallas          texas                     fiction   
306794        dallas          texas                         NaN   

                       publisher language           book_author  
0          HarperFlamingo Canada       en  Richard Bruce Wright  
1          HarperFlamingo Canada       en  Richard Bruce Wright  
2          HarperFlamingo Canada       en  Richard Bruce Wright  
3          HarperFlamingo Canada       en  Richard Bruce Wright  
4          HarperFlamingo Canada       en  Richard Bruce Wright  
...                          ...      ...                   ...  
306790    Simon & Schuster Audio      NaN         David Gardner  
306791              Pocket Books       en         P.J. O'Rourke  
306792           Lone Star Books      NaN         Claude Dooley  
306793                Kqed Books       en          Jeremy Lloyd  
306794  American Map Corporation      NaN                Mapsco  

[306795 rows x 12 columns]